In [84]:
%pip install transformer_lens
%pip install wandb

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Note: you may need to restart the kernel to use updated packages.


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Note: you may need to restart the kernel to use updated packages.


In [85]:
import torch
import numpy as np
from functools import partial
import einops
import random
import pprint
import json
from pathlib import Path
from transformer_lens import HookedTransformer
from transformer_lens.utils import (
    load_dataset,
    tokenize_and_concatenate,
    get_act_name,
    download_file_from_hf,
)
import tqdm
from torch import nn
from torch.nn import functional as F
import wandb
# %%

In [86]:
default_cfg = {
    "seed": 43,
    "batch_size": 4096,
    "buffer_mult": 384,
    "lr": 1e-4,
    "num_tokens": int(2e9), #5525253
    "l1_coeff": 3e-4,
    "beta1": 0.9,
    "beta2": 0.99,
    "dict_mult": 8,
    "seq_len": 1024, #1024,
    "enc_dtype":"fp32",
    "remove_rare_dir": False,
    "model_name": "gelu-1l",
    "site": "mlp_out",
    "layer": 0,
    "device": "cuda"
}
    
site_to_size = {
    "mlp_out": 512,
    "post": 2048,
    "resid_pre": 512,
    "resid_mid": 512,
    "resid_post": 512,
}

# %%
def post_init_cfg(cfg):
    cfg["model_batch_size"] = cfg["batch_size"] // cfg["seq_len"] * 16
    cfg["buffer_size"] = cfg["batch_size"] * cfg["buffer_mult"]
    cfg["buffer_batches"] = cfg["buffer_size"] // cfg["seq_len"]
    cfg["act_name"] = get_act_name(cfg["site"], cfg["layer"])
    cfg["act_size"] = site_to_size[cfg["site"]]
    cfg["dict_size"] = cfg["act_size"] * cfg["dict_mult"]
    cfg["name"] = f"{cfg['model_name']}_{cfg['layer']}_{cfg['dict_size']}_{cfg['site']}"
cfg = default_cfg
post_init_cfg(cfg)
pprint.pprint(cfg)
# %%
post_init_cfg(cfg)
pprint.pprint(cfg)

{'act_name': 'blocks.0.hook_mlp_out',
 'act_size': 512,
 'batch_size': 4096,
 'beta1': 0.9,
 'beta2': 0.99,
 'buffer_batches': 1536,
 'buffer_mult': 384,
 'buffer_size': 1572864,
 'device': 'cuda',
 'dict_mult': 8,
 'dict_size': 4096,
 'enc_dtype': 'fp32',
 'l1_coeff': 0.0003,
 'layer': 0,
 'lr': 0.0001,
 'model_batch_size': 64,
 'model_name': 'gelu-1l',
 'name': 'gelu-1l_0_4096_mlp_out',
 'num_tokens': 2000000000,
 'remove_rare_dir': False,
 'seed': 43,
 'seq_len': 1024,
 'site': 'mlp_out'}
{'act_name': 'blocks.0.hook_mlp_out',
 'act_size': 512,
 'batch_size': 4096,
 'beta1': 0.9,
 'beta2': 0.99,
 'buffer_batches': 1536,
 'buffer_mult': 384,
 'buffer_size': 1572864,
 'device': 'cuda',
 'dict_mult': 8,
 'dict_size': 4096,
 'enc_dtype': 'fp32',
 'l1_coeff': 0.0003,
 'layer': 0,
 'lr': 0.0001,
 'model_batch_size': 64,
 'model_name': 'gelu-1l',
 'name': 'gelu-1l_0_4096_mlp_out',
 'num_tokens': 2000000000,
 'remove_rare_dir': False,
 'seed': 43,
 'seq_len': 1024,
 'site': 'mlp_out'}


In [87]:
SEED = cfg["seed"]
GENERATOR = torch.manual_seed(SEED)
DTYPES = {"fp32": torch.float32, "fp16": torch.float16, "bf16": torch.bfloat16}
np.random.seed(SEED)
random.seed(SEED)
torch.set_grad_enabled(True)

model = HookedTransformer.from_pretrained(cfg["model_name"]).to(DTYPES[cfg["enc_dtype"]]).to(cfg["device"])

# from parallel import DataParallelModel, DataParallelCriterion
# model = torch.nn.DataParallel(raw_model)

# n_layers = model.cfg.n_layers
# d_model = model.cfg.d_model
# n_heads = model.cfg.n_heads
# d_head = model.cfg.d_head
# d_mlp = model.cfg.d_mlp
# d_vocab = model.cfg.d_vocab
next(model.parameters()).device

Loaded pretrained model gelu-1l into HookedTransformer
Changing model dtype to torch.float32
Moving model to device:  cuda


device(type='cuda', index=0)

In [88]:
# %%
@torch.no_grad()
def get_acts(tokens, batch_size=1024):
    print(f"{tokens.get_device()=}")
    _, cache = model.run_with_cache(tokens, stop_at_layer=cfg["layer"]+1, names_filter=cfg["act_name"])
    acts = cache[cfg["act_name"]]
    acts = acts.reshape(-1, acts.shape[-1])
    subsample = torch.randperm(acts.shape[0], generator=GENERATOR)[:batch_size]
    subsampled_acts = acts[subsample, :]
    return subsampled_acts, acts
sub, acts = get_acts(torch.arange(20).reshape(2, 10), batch_size=3)
sub.shape, acts.shape

tokens.get_device()=-1


(torch.Size([3, 512]), torch.Size([20, 512]))

In [89]:
# %%
SAVE_DIR = Path("cache")
class AutoEncoder(nn.Module):
    def __init__(self, cfg, old_ae=None):
        super().__init__()
        d_hidden = cfg["dict_size"]
        l1_coeff = cfg["l1_coeff"]
        dtype = DTYPES[cfg["enc_dtype"]]
        torch.manual_seed(cfg["seed"])

        if old_ae is not None:
            wenc = torch.nn.init.kaiming_uniform_(torch.empty(cfg["act_size"], d_hidden, dtype=dtype, device=cfg["device"]))
            wenc[:, :old_ae.W_enc.shape[1]] = old_ae.W_enc
            self.W_enc = nn.Parameter(wenc)

            wdec = torch.nn.init.kaiming_uniform_(torch.empty(d_hidden, cfg["act_size"], dtype=dtype, device=cfg["device"]))
            wdec[:old_ae.W_dec.shape[0], :] = old_ae.W_dec
            self.W_dec = nn.Parameter(wdec)
            
            benc = torch.zeros(d_hidden, dtype=dtype, device=cfg["device"])
            benc[:old_ae.b_enc.shape[0]] = old_ae.b_enc
            self.b_enc = nn.Parameter(benc)
            self.b_dec = nn.Parameter(old_ae.b_dec)

            #TODO may need to normalize
            # self.W_dec.data[:] = self.W_dec / self.W_dec.norm(dim=-1, keepdim=True)
            print("~~~~~~~~~~~ INIT AND NOOOO NORMALIZED!")
        else:
            self.W_enc = nn.Parameter(torch.nn.init.kaiming_uniform_(torch.empty(cfg["act_size"], d_hidden, dtype=dtype, device=cfg["device"])))
            self.W_dec = nn.Parameter(torch.nn.init.kaiming_uniform_(torch.empty(d_hidden, cfg["act_size"], dtype=dtype, device=cfg["device"])))
            self.b_enc = nn.Parameter(torch.zeros(d_hidden, dtype=dtype, device=cfg["device"]))
            self.b_dec = nn.Parameter(torch.zeros(cfg["act_size"], dtype=dtype, device=cfg["device"]))

            self.W_dec.data[:] = self.W_dec / self.W_dec.norm(dim=-1, keepdim=True)

        self.d_hidden = d_hidden
        self.l1_coeff = l1_coeff

        self.to(cfg["device"])

    def forward(self, x):
        x_cent = x - self.b_dec
        acts = F.relu(x_cent @ self.W_enc + self.b_enc)
        print(f"{acts.shape=}")
        acts = acts.clone()
        acts[..., 240] = 0
        x_reconstruct = acts @ self.W_dec + self.b_dec
        l2_loss = (x_reconstruct.float() - x.float()).pow(2).sum(-1).mean(0)
        l1_loss = self.l1_coeff * (acts.float().abs().sum())
        loss = l2_loss + l1_loss
        return loss, x_reconstruct, acts, l2_loss, l1_loss

    @torch.no_grad()
    def make_decoder_weights_and_grad_unit_norm(self):
        W_dec_normed = self.W_dec / self.W_dec.norm(dim=-1, keepdim=True)
        W_dec_grad_proj = (self.W_dec.grad * W_dec_normed).sum(-1, keepdim=True) * W_dec_normed
        self.W_dec.grad -= W_dec_grad_proj
        # Bugfix(?) for ensuring W_dec retains unit norm, this was not there when I trained my original autoencoders.
        self.W_dec.data = W_dec_normed

    def get_version(self):
        version_list = [int(file.name.split(".")[0]) for file in list(SAVE_DIR.iterdir()) if "pt" in str(file)]
        if len(version_list):
            return 1+max(version_list)
        else:
            return 0

    def save(self):
        version = self.get_version()
        torch.save(self.state_dict(), SAVE_DIR/(str(version)+".pt"))
        with open(SAVE_DIR/(str(version)+"_cfg.json"), "w") as f:
            json.dump(cfg, f)
        print("Saved as version", version)

    @classmethod
    def load(cls, version):
        cfg = (json.load(open(SAVE_DIR/(str(version)+"_cfg.json"), "r")))
        pprint.pprint(cfg)
        self = cls(cfg=cfg)
        self.load_state_dict(torch.load(SAVE_DIR/(str(version)+".pt")))
        return self

    @classmethod
    def load_from_hf(cls, version):
        """
        Loads the saved autoencoder from HuggingFace.

        Version is expected to be an int, or "run1" or "run2"

        version 25 is the final checkpoint of the first autoencoder run,
        version 47 is the final checkpoint of the second autoencoder run.
        """
        if version=="run1":
            version = 25
        elif version=="run2":
            version = 47

        cfg = download_file_from_hf("NeelNanda/sparse_autoencoder", f"{version}_cfg.json")
        pprint.pprint(cfg)
        self = cls(cfg=cfg)
        self.load_state_dict(download_file_from_hf("NeelNanda/sparse_autoencoder", f"{version}.pt", force_is_torch=True))
        return self

# %%
def shuffle_data(all_tokens):
    print("Shuffled data")
    return all_tokens[torch.randperm(all_tokens.shape[0])]
    
    # torch.save(all_tokens_reshaped, "data/c4_code_2b_tokens_reshaped_filtered.pt")
# else:
    # data = datasets.load_from_disk("/Users/wenx/Documents/playground/translation/data/c4_code_tokenized_2b.hf")
    # all_tokens = torch.load("data/c4-10k.pt")
    # all_tokens = shuffle_data(all_tokens)


# %%

In [90]:
## FILTER DATA
# encoder = AutoEncoder(cfg, old_ae)

DATA_DIR = Path("data/")
loading_data_first_time = False
if loading_data_first_time:
    data = load_dataset("NeelNanda/c4-code-tokenized-2b", split="train") # c4-code-tokenized-2b
    # data = tokenize_and_concatenate(data, model.tokenizer, max_length=128)
    data.set_format(type="torch", columns=["tokens"])
    all_tokens = data["tokens"].to(cfg["device"])
    print(f"{all_tokens.shape=}")

    all_tokens_reshaped = einops.rearrange(all_tokens, "batch (x seq_len) -> (batch x) seq_len", x=8, seq_len=128)
    all_tokens_reshaped[:, 0] = model.tokenizer.bos_token_id
    all_tokens_reshaped = all_tokens_reshaped[torch.randperm(all_tokens_reshaped.shape[0])]
    print(f"{all_tokens_reshaped.shape=}")

    all_tokens = all_tokens_reshaped

    # check_hyphen = all_tokens == 15
    # all_tokens = all_tokens[check_hyphen.sum(-1)>0]
    # print(f"{all_tokens.shape=}")

@torch.inference_mode()
def get_activating_tokens(
    tokens, #: Int[Tensor, "batch seq"],
    model, #: HookedTransformer,
    autoencoder, #: AutoEncoder,
    feature_idx: int,
    autoencoder_B: bool = False,
): # -> Int[Tensor, "batch seq"]:
    '''
    Returns the indices & values for the highest-activating tokens in the given batch of data.
    '''
    batch, seq = tokens.shape
    _, cache = model.run_with_cache(tokens, names_filter=['blocks.0.hook_mlp_out'])
    mlp_out = cache['blocks.0.hook_mlp_out']

    no_bias = mlp_out - autoencoder.b_dec
    actsf_raw = einops.einsum(autoencoder.W_enc[:, feature_idx], no_bias, "d_model, batch seq d_model -> batch seq")

    has_activated = actsf_raw.abs() > 2
    check_seq = has_activated.sum(-1) # num of tokens in the sequence activate the feature
    result = tokens[check_seq > 0]
    # print(f"{result.shape=}")
    return result



In [91]:
if loading_data_first_time:
    encoder = AutoEncoder.load(16)
    # get_activating_tokens(all_tokens[range(0, 100), :], model, encoder, 240)
    tokens = None #torch.load("data/c4_code_tokenized_2b_filtered_10000.pt")
    step_size = 125
    for i in range((all_tokens.shape[0] // step_size) + 1):
        if i % 100 == 0:
            print(i)
        if i % 1000 == 0:
            torch.save(tokens, f"data/c4_code_tokenized_2b_filtered_{i}.pt")
        range_s = i * step_size
        range_e = min((i+1) * step_size, all_tokens.shape[0])
        filtered = get_activating_tokens(all_tokens[range(range_s, range_e)], model, encoder, 240)
        if tokens == None:
            tokens = filtered
        else:
            tokens = torch.concat((tokens, filtered), dim=0)
            # print(f"{tokens.shape=}")
    all_tokens = tokens
    torch.save(all_tokens, "data/c4_code_tokenized_2b_filtered_7500.pt")
else:
    all_tokens = torch.load("data/c4_code_tokenized_2b_filtered_1000.pt")
    all_tokens = shuffle_data(all_tokens)

print(f"{all_tokens.shape=}")

/tmp/ipykernel_2820/2713894199.py:22: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  all_tokens = torch.load("data/c4_code_tokenized_2b_filtered_1000.pt")


Shuffled data
all_tokens.shape=torch.Size([124610, 1024])


In [92]:
# %%
def replacement_hook(mlp_post, hook, encoder):
    mlp_post_reconstr = encoder(mlp_post)[1]
    return mlp_post_reconstr

def mean_ablate_hook(mlp_post, hook):
    mlp_post[:] = mlp_post.mean([0, 1])
    return mlp_post

def zero_ablate_hook(mlp_post, hook):
    mlp_post[:] = 0.
    return mlp_post

@torch.no_grad()
def get_recons_loss(num_batches=5, local_encoder=None):
    if local_encoder is None:
        local_encoder = encoder
    loss_list = []
    for i in range(num_batches):
        tokens = all_tokens[torch.randperm(len(all_tokens))[:cfg["model_batch_size"]]]
        loss = model(tokens, return_type="loss")
        recons_loss = model.run_with_hooks(tokens, return_type="loss", fwd_hooks=[(cfg["act_name"], partial(replacement_hook, encoder=local_encoder))])
        # mean_abl_loss = model.run_with_hooks(tokens, return_type="loss", fwd_hooks=[(cfg["act_name"], mean_ablate_hook)])
        zero_abl_loss = model.run_with_hooks(tokens, return_type="loss", fwd_hooks=[(cfg["act_name"], zero_ablate_hook)])
        loss_list.append((loss, recons_loss, zero_abl_loss))
    losses = torch.tensor(loss_list)
    loss, recons_loss, zero_abl_loss = losses.mean(0).tolist()

    print(loss, recons_loss, zero_abl_loss)
    score = ((zero_abl_loss - recons_loss)/(zero_abl_loss - loss))
    print(f"{score:.2%}")
    # print(f"{((zero_abl_loss - mean_abl_loss)/(zero_abl_loss - loss)).item():.2%}")
    return score, loss, recons_loss, zero_abl_loss
# print(get_recons_loss())
# %%
# Frequency
@torch.no_grad()
def get_freqs(num_batches=25, local_encoder=None):
    if local_encoder is None:
        local_encoder = encoder
    act_freq_scores = torch.zeros(local_encoder.d_hidden, dtype=torch.float32, device=cfg["device"])
    total = 0
    for i in tqdm.trange(num_batches):
        tokens = all_tokens[torch.randperm(len(all_tokens))[:cfg["model_batch_size"]]]

        _, cache = model.run_with_cache(tokens, stop_at_layer=cfg["layer"]+1, names_filter=cfg["act_name"])
        acts = cache[cfg["act_name"]]
        acts = acts.reshape(-1, cfg["act_size"])

        hidden = local_encoder(acts)[2]

        act_freq_scores += (hidden > 0).sum(0)
        total+=hidden.shape[0]
    act_freq_scores /= total
    num_dead = (act_freq_scores==0).float().mean()
    print("Num dead", num_dead)
    return act_freq_scores
# %%
@torch.no_grad()
def re_init(indices, encoder):
    new_W_enc = (torch.nn.init.kaiming_uniform_(torch.zeros_like(encoder.W_enc)))
    new_W_dec = (torch.nn.init.kaiming_uniform_(torch.zeros_like(encoder.W_dec)))
    new_b_enc = (torch.zeros_like(encoder.b_enc))
    print(new_W_dec.shape, new_W_enc.shape, new_b_enc.shape)
    encoder.W_enc.data[:, indices] = new_W_enc[:, indices]
    encoder.W_dec.data[indices, :] = new_W_dec[indices, :]
    encoder.b_enc.data[indices] = new_b_enc[indices]


In [93]:
# %%
class Buffer():
    """
    This defines a data buffer, to store a bunch of MLP acts that can be used to train the autoencoder. It'll automatically run the model to generate more when it gets halfway empty.
    """
    def __init__(self, cfg):
        self.buffer = torch.zeros((cfg["buffer_size"], cfg["act_size"]), dtype=torch.bfloat16, requires_grad=False, device=cfg["device"])
        self.cfg = cfg
        self.token_pointer = 0
        self.first = True
        self.refresh()

    @torch.no_grad()
    def refresh(self):

        self.pointer = 0
        with torch.autocast("cuda", torch.bfloat16):
            if self.first:
                num_batches = self.cfg["buffer_batches"]
            else:
                num_batches = self.cfg["buffer_batches"]//2
            self.first = False
            # print(f"{all_tokens.shape=}")
            # print(f"{num_batches=}")
            # print(self.cfg["model_batch_size"])
            # print(f"{=}")
            for _ in range(0, num_batches, self.cfg["model_batch_size"]):
                tokens = all_tokens[self.token_pointer:self.token_pointer+self.cfg["model_batch_size"]]
                _, cache = model.run_with_cache(tokens, stop_at_layer=cfg["layer"]+1, names_filter=cfg["act_name"])
                acts = cache[cfg["act_name"]].reshape(-1, self.cfg["act_size"])
                # print(f"{tokens.shape=}")
                # print(f"{acts.shape=}")
                # print(f"{self.pointer=}")
                # print(f"{self.buffer.shape=}")
                # print(cache[cfg["act_name"]].shape)
                # print(tokens.shape, acts.shape, self.pointer, self.token_pointer)
                self.buffer[self.pointer: self.pointer+acts.shape[0]] = acts
                self.pointer += acts.shape[0]
                self.token_pointer += self.cfg["model_batch_size"]
                # if self.token_pointer > all_tokens.shape[0] - self.cfg["model_batch_size"]:
                #     self.token_pointer = 0

        self.pointer = 0
        self.buffer = self.buffer[torch.randperm(self.buffer.shape[0])]

    @torch.no_grad()
    def next(self):
        out = self.buffer[self.pointer:self.pointer+self.cfg["batch_size"]]
        self.pointer += self.cfg["batch_size"]
        if self.pointer > self.buffer.shape[0]//2 - self.cfg["batch_size"]:
            # print("Refreshing the buffer!")
            self.refresh()
        return out

In [94]:
# %% TRAIN
old_ae = AutoEncoder.load(16)
encoder = AutoEncoder(cfg, old_ae)
# encoder = AutoEncoder(cfg)
buffer = Buffer(cfg)
# Code used to remove the "rare freq direction", the shared direction among the ultra low frequency features.
# I experimented with removing it and retraining the autoencoder.
if cfg["remove_rare_dir"]:
    rare_freq_dir = torch.load("rare_freq_dir.pt")
    rare_freq_dir.requires_grad = False

# %%
try:
    wandb.init(project="sae-gelu-1l-mlp-out")
    num_batches = cfg["num_tokens"] // cfg["batch_size"]
    print(f"{num_batches=}")
    # model_num_batches = cfg["model_batch_size"] * num_batches
    encoder_optim = torch.optim.Adam(encoder.parameters(), lr=cfg["lr"], betas=(cfg["beta1"], cfg["beta2"]))
    recons_scores = []
    act_freq_scores_list = []
    for i in tqdm.trange(num_batches):
        i = i % all_tokens.shape[0]
        acts = buffer.next()
        loss, x_reconstruct, mid_acts, l2_loss, l1_loss = encoder(acts)
        loss.backward()
        encoder.make_decoder_weights_and_grad_unit_norm()
        encoder_optim.step()
        encoder_optim.zero_grad()
        loss_dict = {"loss": loss.item(), "l2_loss": l2_loss.item(), "l1_loss": l1_loss.item()}
        del loss, x_reconstruct, mid_acts, l2_loss, l1_loss, acts
        if (i) % 100 == 0:
            wandb.log(loss_dict)
            print(loss_dict)
        if (i) % 1000 == 0:
            x = (get_recons_loss(local_encoder=encoder))
            print("Reconstruction:", x)
            recons_scores.append(x[0])
            freqs = get_freqs(5, local_encoder=encoder)
            act_freq_scores_list.append(freqs)
            # histogram(freqs.log10(), marginal="box", histnorm="percent", title="Frequencies")
            wandb.log({
                "recons_score": x[0],
                "dead": (freqs==0).float().mean().item(),
                "below_1e-6": (freqs<1e-6).float().mean().item(),
                "below_1e-5": (freqs<1e-5).float().mean().item(),
            })
        if (i+1) % 2000 == 0:
            encoder.save()
        if (i+1) % 30000 == 0:
            wandb.log({"reset_neurons": 0.0})
            freqs = get_freqs(50, local_encoder=encoder)
            to_be_reset = (freqs<10**(-5.5))
            print("Resetting neurons!", to_be_reset.sum())
            re_init(to_be_reset, encoder)

except Exception as e:
    print(e.message)
finally:
    encoder.save()
# %%

{'act_name': 'blocks.0.hook_mlp_out',
 'act_size': 512,
 'batch_size': 4096,
 'beta1': 0.9,
 'beta2': 0.99,
 'buffer_batches': 1536,
 'buffer_mult': 384,
 'buffer_size': 1572864,
 'device': 'cuda',
 'dict_mult': 1,
 'dict_size': 512,
 'enc_dtype': 'fp32',
 'l1_coeff': 0.0003,
 'layer': 0,
 'lr': 0.0001,
 'model_batch_size': 64,
 'model_name': 'gelu-1l',
 'name': 'gelu-1l_0_512_mlp_out',
 'num_tokens': 2000000000,
 'remove_rare_dir': False,
 'seed': 49,
 'seq_len': 1024,
 'site': 'mlp_out'}
~~~~~~~~~~~ INIT AND NOOOO NORMALIZED!


/tmp/ipykernel_2820/2692109769.py:80: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  self.load_state_dict(torch.load(SAVE_DIR/(str(version)+".pt")))


num_batches=488281


  0%|          | 0/488281 [00:00<?, ?it/s]

acts.shape=torch.Size([4096, 4096])
{'loss': 1490.86474609375, 'l2_loss': 722.5718994140625, 'l1_loss': 768.2927856445312}
acts.shape=torch.Size([64, 1024, 4096])
acts.shape=torch.Size([64, 1024, 4096])
acts.shape=torch.Size([64, 1024, 4096])
acts.shape=torch.Size([64, 1024, 4096])
acts.shape=torch.Size([64, 1024, 4096])
3.83747935295105 5.80426025390625 8.924461364746094
61.34%
Reconstruction: (0.6133697944292156, 3.83747935295105, 5.80426025390625, 8.924461364746094)


...

 29%|██▉       | 141989/488281 [30:16<43:24, 132.98it/s]

acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096,

 29%|██▉       | 142012/488281 [30:16<1:13:48, 78.18it/s]


acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
{'loss': 123.68717956542969, 'l2_loss': 67.21591186523438, 'l1_loss': 56.47126770019531}
acts.shape=torch.Size([4096, 4096])
acts.shape=torch.Size([4096, 4096])
Saved as version 87


KeyboardInterrupt: 